In [15]:
import cv2 as cv
import mediapipe as mp
import numpy as np
import tensorflow as tf
import time
import datetime
import sqlite3
from tensorflow.keras.models import load_model

In [16]:
conn = sqlite3.connect("analayses.db")
c = conn.cursor()

In [17]:
c.execute("CREATE TABLE IF NOT EXISTS iris_movement ( id INTEGER PRIMARY KEY AUTOINCREMENT,direction TEXT, start_time TIMESTAMP,end_time TIMESTAMP)")
c.execute("CREATE TABLE IF NOT EXISTS hand_movement (id INTEGER PRIMARY KEY AUTOINCREMENT,direction TEXT, start_time TIMESTAMP,end_time TIMESTAMP)")
c.execute("CREATE TABLE IF NOT EXISTS face_movement (id INTEGER PRIMARY KEY AUTOINCREMENT,direction TEXT, start_time TIMESTAMP,end_time TIMESTAMP)")


In [18]:
c.fetchall()

[]

In [190]:

# IRIS TRACKER
class IrisTracker:
    def __init__(self, mp_face_mesh=mp.solutions.face_mesh, max_num_faces=1, refine_landmarks=True, min_detection_confidence=0.5, min_tracking_confidence=0.5):
        self.mp_face_mesh = mp_face_mesh
        self.LEFT_EYE = [362, 382, 381, 380, 374, 373, 390, 249, 263, 466, 388, 387, 386, 385, 384, 398]
        self.RIGHT_EYE = [33, 7, 163, 144, 145, 153, 154, 155, 133, 173, 157, 158, 159, 160, 161, 246]
        self.LEFT_IRIS = [474, 475, 476, 477]
        self.RIGHT_IRIS = [469, 470, 471, 472]
        self.face_mesh = mp_face_mesh.FaceMesh(
            max_num_faces=max_num_faces,
            refine_landmarks=refine_landmarks,
            min_detection_confidence=min_detection_confidence,
            min_tracking_confidence=min_tracking_confidence
        )
        self.left_direction = None
        self.right_direction = None

    def frame_settings(self, frame):
        self.frame = cv.flip(frame, 1)
        self.rgb_frame = cv.cvtColor(self.frame, cv.COLOR_BGR2RGB)
        self.img_h, self.img_w = self.frame.shape[:2]
        self.results = self.face_mesh.process(self.rgb_frame)

        if self.results.multi_face_landmarks:
            self.mesh_points = np.array([np.multiply([p.x, p.y], [self.img_w, self.img_h]).astype(int) for p in
                                         self.results.multi_face_landmarks[0].landmark])
        return self.frame

    def get_eyes(self):
        if self.results.multi_face_landmarks:
            self.left_eye_points = self.mesh_points[self.LEFT_EYE]
            self.right_eye_points = self.mesh_points[self.RIGHT_EYE]
            self.left_iris_points = self.mesh_points[self.LEFT_IRIS]
            self.right_iris_points = self.mesh_points[self.RIGHT_IRIS]

            self.left_direction = self.get_eye_direction(self.left_eye_points, self.left_iris_points)
            self.right_direction = self.get_eye_direction(self.right_eye_points, self.right_iris_points)

    def get_eye_direction(self, eye_points, iris_points):
        if self.results.multi_face_landmarks:
            eye_left = min(eye_points[:, 0])
            eye_right = max(eye_points[:, 0])
            eye_top = min(eye_points[:, 1])
            eye_bottom = max(eye_points[:, 1])
            eye_width = eye_right - eye_left
            eye_height = eye_bottom - eye_top

            iris_center = np.mean(iris_points, axis=0)

            if iris_center[0] < eye_left + 0.4 * eye_width:
                return "Left"
            elif iris_center[0] > eye_right - 0.4 * eye_width:
                return "Right"
            elif iris_center[1] < eye_top + 0.4 * eye_height:
                return "Up"
            elif iris_center[1] > eye_bottom - 0.4 * eye_height:
                return "Down"
            else:
                return "Center"

    def put_text_to_screen(self, frame):
        if self.results.multi_face_landmarks:
            cv.putText(frame, "Right Eye" + self.left_direction, (10, 30), cv.FONT_HERSHEY_SIMPLEX, 0.7,
                       (255, 0, 255), 2)
            cv.putText(frame, "Left Eye" + self.right_direction, (10, 60), cv.FONT_HERSHEY_SIMPLEX, 0.7,
                       (255, 0, 255), 2)
        return frame

    def circle_to_screen(self, frame):
        if self.results.multi_face_landmarks:
            (l_cx, l_cy), l_radius = cv.minEnclosingCircle(self.left_iris_points)
            (r_cx, r_cy), r_radius = cv.minEnclosingCircle(self.right_iris_points)

            center_left = np.array([l_cx, l_cy], dtype=np.int32)
            center_right = np.array([r_cx, r_cy], dtype=np.int32)

            cv.circle(frame, center_left, int(l_radius), (255, 0, 255), 1, cv.LINE_AA)
            cv.circle(frame, center_right, int(r_radius), (255, 0, 255), 1, cv.LINE_AA)
        return frame
    
def run_iris(iris, frame):
    frame = iris.frame_settings(frame)
    iris.get_eyes()
    frame = iris.put_text_to_screen(frame)
    frame = iris.circle_to_screen(frame)
    iris.get_eyes()
    return frame

In [191]:
video = cv.VideoCapture('Data/video.mp4')  # Video dosyasının adını ve yolunu uygun şekilde güncelle
iris = IrisTracker()

while True:
    ret, frame = video.read()
    if not ret:
        break

    processed_frame = run_iris(iris, frame)

    # Veritabanına kaydetmek için gerekli işlemleri yap
    if iris.left_direction is not None:
        direction = iris.left_direction  # Sol göz hareket yönünü al
        timestamp = datetime.datetime.now()
        c.execute("INSERT INTO iris_movement (direction, start_time, end_time) VALUES (?,?,?)",
                  (direction, timestamp, timestamp))
        conn.commit()

    if iris.right_direction is not None:
        direction = iris.right_direction  # Sağ göz hareket yönünü al
        timestamp = datetime.datetime.now()

        c.execute("INSERT INTO iris_movement (direction, start_time, end_time) VALUES (?,?,?)",
                  (direction, timestamp, timestamp))
        conn.commit()

    cv.imshow('Frame', processed_frame)
    if cv.waitKey(1) & 0xFF == ord('q'):
        break

video.release()
cv.destroyAllWindows()


In [21]:
# EL TRACKER
class HandTracker:
    def __init__(self, mp_hands=mp.solutions.hands, max_num_hands=2, min_detection_confidence=0.5, min_tracking_confidence=0.5):
        self.mp_hands = mp_hands
        self.hands = mp_hands.Hands(
            max_num_hands=max_num_hands,
            min_detection_confidence=min_detection_confidence,
            min_tracking_confidence=min_tracking_confidence
        )
        self.direction = None

    def track_hand(self, frame):
        self.frame = cv.flip(frame, 1)
        self.rgb_frame = cv.cvtColor(self.frame, cv.COLOR_BGR2RGB)
        self.results = self.hands.process(self.rgb_frame)

        if self.results.multi_hand_landmarks:
            landmarks = self.results.multi_hand_landmarks[0].landmark
            hand_center = (landmarks[9].x, landmarks[9].y)
            thumb_tip = (landmarks[4].x, landmarks[4].y)
            index_tip = (landmarks[8].x, landmarks[8].y)

            thumb_angle = np.arctan2(hand_center[1] - thumb_tip[1], hand_center[0] - thumb_tip[0])
            index_angle = np.arctan2(hand_center[1] - index_tip[1], hand_center[0] - index_tip[0])
            angle_diff = np.degrees(index_angle - thumb_angle)

            if angle_diff < -10:
                self.direction = "Left"
            elif angle_diff > 10:
                self.direction = "Right"
            else:
                self.direction = "Center"

    def put_text_to_screen(self, frame):
        if self.direction is not None:
            cv.putText(frame, "El: " + self.direction, (10, 30), cv.FONT_HERSHEY_SIMPLEX, 0.7, (255, 0, 255), 2)
        return frame


def run_hand(hand_tracker, frame):
    hand_tracker.track_hand(frame)
    frame = hand_tracker.put_text_to_screen(frame)
    return frame


In [192]:
# Video oynatıcıyı başlat
cap = cv.VideoCapture("Data/video.mp4")  # Video dosya adını güncelleyin
hand_tracker = HandTracker()

# Video üzerinde döngü
while True:
    ret, frame = cap.read()
    if not ret:
        break
    
    # El takibi
    hand_tracker.track_hand(frame)
    
    # El hareketini veritabanına kaydet
    if hand_tracker.direction is not None:
        direction = hand_tracker.direction  # El hareket yönünü al
        timestamp = datetime.datetime.now()  # Geçerli zamanı al

        c.execute("INSERT INTO hand_movement (direction, start_time, end_time) VALUES (?,?,?)",
                (direction, timestamp, timestamp))
        conn.commit()

    # Ekrana metin ve işaretçiyi yerleştir
    frame = hand_tracker.put_text_to_screen(frame)

    # Görüntüyü göster
    cv.imshow("Video", frame)

    # Çıkış için 'q' tuşuna basılmasını kontrol et
    if cv.waitKey(1) & 0xFF == ord('q'):
        break

# Kaynakları serbest bırak ve pencereyi kapat
cap.release()
cv.destroyAllWindows()

In [25]:
class FaceTracker:
    def __init__(self, classifier='haarcascades/haarcascade_frontalface_default.xml'):
        self.haar_cascade = cv.CascadeClassifier(classifier)
        self.prev_face_rect = None  # Önceki karedeki yüz dikdörtgeninin konumu

    def frame_settings(self, frame, size=(600, 400), color=cv.COLOR_BGR2GRAY, scale=1.1, minNeighbors=9):
        self.frame = cv.resize(frame, size)
        self.gray = cv.cvtColor(frame, color)
        self.faces_rect = self.haar_cascade.detectMultiScale(self.gray, scaleFactor=scale, minNeighbors=minNeighbors)
        return self.faces_rect

    def draw_rect(self, frame, faces_rect, rgb=(0, 255, 0), thickness=2):
        for (x, y, w, h) in faces_rect:
            cv.rectangle(frame, (x, y), (x + w, y + h), rgb, thickness=thickness)

            # Yüz hareket yönünü belirle
            if self.prev_face_rect is not None:
                prev_face_x = self.prev_face_rect[0]
                curr_face_x = x
                if curr_face_x > prev_face_x:
                    direction = "Right"
                else:
                    direction = "Left"
            else:
                direction = "Unknown"

            # Görüntüye yönü yazdır
            cv.putText(frame, direction, (x, y - 10), cv.FONT_HERSHEY_SIMPLEX, 0.9, rgb, thickness)

            # Veritabanına veri ekle
            start_time = datetime.datetime.now()
            end_time = datetime.datetime.now()
            c.execute("INSERT INTO face_movement (direction, start_time, end_time) VALUES (?, ?, ?)",(direction, start_time, end_time))
            conn.commit()

            # Önceki karedeki yüz dikdörtgenini güncelle
            self.prev_face_rect = (x, y, w, h)

        return frame


def run_face(face, frame):
    faces_rect = face.frame_settings(frame)
    frame = face.draw_rect(frame, faces_rect)
    return frame

In [27]:
# Video oynatıcıyı başlat
cap = cv.VideoCapture("Data/video.mp4")  # Video dosya adını güncelleyin
face_tracker = FaceTracker()

# Video üzerinde döngü
while True:
    ret, frame = cap.read()
    if not ret:
        break

    # Yüz takibi
    frame = run_face(face_tracker, frame)

    # Görüntüyü göster
    cv.imshow("Video", frame)

    # Çıkış için 'q' tuşuna basılmasını kontrol et
    if cv.waitKey(1) & 0xFF == ord('q'):
        break

# Kaynakları serbest bırak ve pencereyi kapat
cap.release()
cv.destroyAllWindows()

In [28]:
# Veritabanı bağlantısını kapat
conn.close()


In [33]:
# Veritabanına bağlan
conn = sqlite3.connect('analayses.db')
c = conn.cursor()

# Veritabanından verileri çek
c.execute("SELECT * FROM face_movement")
face_movement = c.fetchall()

c.execute("SELECT * FROM hand_movement")
hand_movement = c.fetchall()

c.execute("SELECT * FROM iris_movement")
iris_movement = c.fetchall()

# Verileri analiz et ve raporla
# Yapmak istediğiniz analiz işlemlerini gerçekleştirin

# Raporu oluştur ve çıktıyı göster veya kaydet


In [34]:
c.fetchall()

[]

In [50]:
import pandas as pd


In [52]:
df_iris= pd.DataFrame(iris_movement, columns=["id", "direction", "start_time", "end_time"])

In [53]:
df_face = pd.DataFrame(face_movement, columns=["id", "direction", "start_time", "end_time"])


In [54]:
df_hand= pd.DataFrame(face_movement, columns=["id", "direction", "start_time", "end_time"])

In [55]:
df_iris.head()

id direction                  start_time                    end_time
0   1        Up  2023-06-15 01:56:55.070381  2023-06-15 01:56:55.070381
1   2        Up  2023-06-15 01:56:55.078380  2023-06-15 01:56:55.078380
2   3        Up  2023-06-15 01:56:55.130557  2023-06-15 01:56:55.130557
3   4    Center  2023-06-15 01:56:55.138549  2023-06-15 01:56:55.138549
4   5    Center  2023-06-15 01:56:55.194546  2023-06-15 01:56:55.194546

In [56]:
df_hand.head()

id direction                  start_time                    end_time
0   1      Left  2023-06-15 02:20:45.116573  2023-06-15 02:20:45.116573
1   2      Left  2023-06-15 02:20:45.153527  2023-06-15 02:20:45.153527
2   3      Left  2023-06-15 02:20:45.176956  2023-06-15 02:20:45.176956
3   4      Left  2023-06-15 02:20:45.198998  2023-06-15 02:20:45.198998
4   5      Left  2023-06-15 02:20:45.230557  2023-06-15 02:20:45.230557

In [57]:
df_face.head()

id direction                  start_time                    end_time
0   1      Left  2023-06-15 02:20:45.116573  2023-06-15 02:20:45.116573
1   2      Left  2023-06-15 02:20:45.153527  2023-06-15 02:20:45.153527
2   3      Left  2023-06-15 02:20:45.176956  2023-06-15 02:20:45.176956
3   4      Left  2023-06-15 02:20:45.198998  2023-06-15 02:20:45.198998
4   5      Left  2023-06-15 02:20:45.230557  2023-06-15 02:20:45.230557

In [58]:
df_iris

id direction                  start_time                    end_time
0          1        Up  2023-06-15 01:56:55.070381  2023-06-15 01:56:55.070381
1          2        Up  2023-06-15 01:56:55.078380  2023-06-15 01:56:55.078380
2          3        Up  2023-06-15 01:56:55.130557  2023-06-15 01:56:55.130557
3          4    Center  2023-06-15 01:56:55.138549  2023-06-15 01:56:55.138549
4          5    Center  2023-06-15 01:56:55.194546  2023-06-15 01:56:55.194546
...      ...       ...                         ...                         ...
22877  22878    Center  2023-06-15 09:24:33.180883  2023-06-15 09:24:33.180883
22878  22879        Up  2023-06-15 09:24:33.229945  2023-06-15 09:24:33.229945
22879  22880    Center  2023-06-15 09:24:33.229945  2023-06-15 09:24:33.229945
22880  22881        Up  2023-06-15 09:24:33.278766  2023-06-15 09:24:33.278766
22881  22882    Center  2023-06-15 09:24:33.278766  2023-06-15 09:24:33.278766

[22882 rows x 4 columns]

#### iris direction isimlerinin kalıcı güncellenmesi

In [86]:
df_iris['direction'].replace({'Up': 'Right', 'Center': 'Left'}, inplace=True)


In [87]:
df_iris.head()

id direction                  start_time                    end_time
0   1     Right  2023-06-15 01:56:55.070381  2023-06-15 01:56:55.070381
1   2     Right  2023-06-15 01:56:55.078380  2023-06-15 01:56:55.078380
2   3     Right  2023-06-15 01:56:55.130557  2023-06-15 01:56:55.130557
3   4      Left  2023-06-15 01:56:55.138549  2023-06-15 01:56:55.138549
4   5      Left  2023-06-15 01:56:55.194546  2023-06-15 01:56:55.194546

In [74]:
df_face

id direction                  start_time                    end_time
0          1      Left  2023-06-15 02:20:45.116573  2023-06-15 02:20:45.116573
1          2      Left  2023-06-15 02:20:45.153527  2023-06-15 02:20:45.153527
2          3      Left  2023-06-15 02:20:45.176956  2023-06-15 02:20:45.176956
3          4      Left  2023-06-15 02:20:45.198998  2023-06-15 02:20:45.198998
4          5      Left  2023-06-15 02:20:45.230557  2023-06-15 02:20:45.230557
...      ...       ...                         ...                         ...
18419  18420     Right  2023-06-15 09:46:14.573274  2023-06-15 09:46:14.573274
18420  18421      Left  2023-06-15 09:46:14.663748  2023-06-15 09:46:14.663748
18421  18422     Right  2023-06-15 09:46:14.759319  2023-06-15 09:46:14.759319
18422  18423     Right  2023-06-15 09:46:14.759319  2023-06-15 09:46:14.759319
18423  18424      Left  2023-06-15 09:46:14.849771  2023-06-15 09:46:14.849771

[18424 rows x 4 columns]

In [61]:
df_hand

id direction                  start_time                    end_time
0          1      Left  2023-06-15 02:20:45.116573  2023-06-15 02:20:45.116573
1          2      Left  2023-06-15 02:20:45.153527  2023-06-15 02:20:45.153527
2          3      Left  2023-06-15 02:20:45.176956  2023-06-15 02:20:45.176956
3          4      Left  2023-06-15 02:20:45.198998  2023-06-15 02:20:45.198998
4          5      Left  2023-06-15 02:20:45.230557  2023-06-15 02:20:45.230557
...      ...       ...                         ...                         ...
18419  18420     Right  2023-06-15 09:46:14.573274  2023-06-15 09:46:14.573274
18420  18421      Left  2023-06-15 09:46:14.663748  2023-06-15 09:46:14.663748
18421  18422     Right  2023-06-15 09:46:14.759319  2023-06-15 09:46:14.759319
18422  18423     Right  2023-06-15 09:46:14.759319  2023-06-15 09:46:14.759319
18423  18424      Left  2023-06-15 09:46:14.849771  2023-06-15 09:46:14.849771

[18424 rows x 4 columns]

### Eksik değerim yok

In [63]:
df_hand.isnull().sum()

id            0
direction     0
start_time    0
end_time      0
dtype: int64

In [64]:
df_face.isnull().sum()

id            0
direction     0
start_time    0
end_time      0
dtype: int64

In [65]:
df_iris.isnull().sum()

id            0
direction     0
start_time    0
end_time      0
dtype: int64

### El hareketleri ne kadar süre ne yönde

In [88]:
from datetime import datetime

def analyze_hand_movements(df_hand):
    # Sağ el hareketleri
    right_hand_count = df_hand[df_hand['direction'] == 'Right']['id'].count()
    right_hand_start = pd.to_datetime(df_hand[df_hand['direction'] == 'Right']['start_time'])
    right_hand_end = pd.to_datetime(df_hand[df_hand['direction'] == 'Right']['end_time'])
    right_hand_duration = (right_hand_end - right_hand_start).sum()

    # Sol el hareketleri
    left_hand_count = df_hand[df_hand['direction'] == 'Left']['id'].count()
    left_hand_start = pd.to_datetime(df_hand[df_hand['direction'] == 'Left']['start_time'])
    left_hand_end = pd.to_datetime(df_hand[df_hand['direction'] == 'Left']['end_time'])
    left_hand_duration = (left_hand_end - left_hand_start).sum()

    return right_hand_count, right_hand_duration, left_hand_count, left_hand_duration

# Veri analizini uygula
right_hand_count, right_hand_duration, left_hand_count, left_hand_duration = analyze_hand_movements(df_hand)

print("Sağ el hareket sayısı:", right_hand_count)
print("Sağ el toplam süre:", right_hand_duration)
print("Sol el hareket sayısı:", left_hand_count)
print("Sol el toplam süre:", left_hand_duration)


Sağ el hareket sayısı: 2319
Sağ el toplam süre: 0 days 00:00:00.017042
Sol el hareket sayısı: 3751
Sol el toplam süre: 0 days 00:00:00.000123


## İris hareketleri ne kadar süre ne yönde

In [89]:
from datetime import datetime

def analyze_hand_movements(df):
    # Sağ el hareketleri
    right_count = df[df['direction'] == 'Right']['id'].count()
    right_start = pd.to_datetime(df[df['direction'] == 'Right']['start_time'])
    right_end = pd.to_datetime(df[df['direction'] == 'Right']['end_time'])
    right_duration = (right_end - right_start).sum()

    # Sol el hareketleri
    left_count = df[df['direction'] == 'Left']['id'].count()
    left_start = pd.to_datetime(df[df['direction'] == 'Left']['start_time'])
    left_end = pd.to_datetime(df[df['direction'] == 'Left']['end_time'])
    left_duration = (left_end - left_start).sum()

    return right_count, right_duration, left_count, left_duration

# Veri analizini uygula
right_iris_count, right_iris_duration, left_iris_count, left_iris_duration = analyze_hand_movements(df_iris)

print("Sağ iris hareket sayısı:", right_iris_count)
print("Sağ iris toplam süre:", right_iris_duration)
print("Sol iris hareket sayısı:", left_iris_count)
print("Sol iris toplam süre:", left_iris_duration)


Sağ iris hareket sayısı: 11031
Sağ iris toplam süre: 0 days 00:00:00
Sol iris hareket sayısı: 11811
Sol iris toplam süre: 0 days 00:00:00


## Yüz hareketleri ne kadar süre hangi yönde

In [90]:
def analyze_face_movements(df_face):
    # Sağ yüz hareketleri
    right_face_count = df_face[df_face['direction'] == 'Right']['id'].count()
    right_face_start = pd.to_datetime(df_face[df_face['direction'] == 'Right']['start_time'])
    right_face_end = pd.to_datetime(df_face[df_face['direction'] == 'Right']['end_time'])
    right_face_duration = (right_face_end - right_face_start).sum()

    # Sol yüz hareketleri
    left_face_count = df_face[df_face['direction'] == 'Left']['id'].count()
    left_face_start = pd.to_datetime(df_face[df_face['direction'] == 'Left']['start_time'])
    left_face_end = pd.to_datetime(df_face[df_face['direction'] == 'Left']['end_time'])
    left_face_duration = (left_face_end - left_face_start).sum()

    return right_face_count, right_face_duration, left_face_count, left_face_duration

# Veri analizini uygula
right_face_count, right_face_duration, left_face_count, left_face_duration = analyze_face_movements(df_face)

print("Sağ yüz hareket sayısı:", right_face_count)
print("Sağ yüz toplam süre:", right_face_duration)
print("Sol yüz hareket sayısı:", left_face_count)
print("Sol yüz toplam süre:", left_face_duration)


Sağ yüz hareket sayısı: 2319
Sağ yüz toplam süre: 0 days 00:00:00.017042
Sol yüz hareket sayısı: 3751
Sol yüz toplam süre: 0 days 00:00:00.000123


## Hareket yön ve zamanları

In [184]:
import pandas as pd

def group_hareketler(df):
    # Veri çerçevesini "Left" ve "Right" hareketlerine göre filtreleyin
    df_filtered = df[(df['direction'] == 'Left') | (df['direction'] == 'Right')]

    # Başlangıç değerlerini tanımlayın
    start_time = None
    end_time = None
    prev_direction = None
    direction_count = 0

    # Gruplanmış hareketleri tutacak bir liste oluşturun
    grouped_hareketler = []

    # Veri çerçevesini döngüye alın
    for index, row in df_filtered.iterrows():
        if start_time is None:  # İlk hareketi belirleyin
            start_time = pd.to_datetime(row['start_time'])
            end_time = pd.to_datetime(row['end_time'])
            prev_direction = row['direction']
            direction_count = 1
        else:  # Ardışık hareketleri gruplayın
            current_start_time = pd.to_datetime(row['start_time'])
            current_end_time = pd.to_datetime(row['end_time'])
            current_direction = row['direction']
            
            # Eğer ardışık hareketler aynı yöndeyse end_time'i güncelleyin
            if current_direction == prev_direction and current_start_time - end_time <= pd.Timedelta(seconds=1):
                end_time = current_end_time
                direction_count += 1
            else:  # Gruplanmış hareketleri listeye ekleyin
                if direction_count > 1:
                    grouped_hareketler.append((prev_direction, direction_count, end_time - start_time))
                else:
                    grouped_hareketler.append((prev_direction, end_time - start_time))
                
                # Yeni bir hareketin başlangıç ve bitiş zamanlarını güncelleyin
                start_time = current_start_time
                end_time = current_end_time
                prev_direction = current_direction
                direction_count = 1

    # Son hareketi gruplanmış hareketlere ekleyin
    if start_time is not None and end_time is not None:
        if direction_count > 1:
            grouped_hareketler.append((prev_direction, direction_count, end_time - start_time))
        else:
            grouped_hareketler.append((prev_direction, end_time - start_time))
    
    return grouped_hareketler

# Veri çerçevesini oluşturun (Örnek olarak bir DataFrame kullanıldı)
df = pd.DataFrame({
    'start_time': ['2023-06-15 02:20:56.654725', '2023-06-15 02:20:56.758532', '2023-06-15 02:20:57.260857',
                   '2023-06-15 02:20:57.391525', '2023-06-15 02:20:57.412303', '2023-06-15 02:20:57.560628'],
    'end_time': ['2023-06-15 02:20:56.758532', '2023-06-15 02:20:57.054182', '2023-06-15 02:20:57.391525',
                 '2023-06-15 02:20:57.412303', '2023-06-15 02:20:57.560628', '2023-06-15 02:20:57.661025'],
    'direction': ['Left', 'Left', 'Left', 'Right', 'Right', 'Left']
})

# Fonksiyonu çağırın ve gruplanmış hareketleri alın
grouped_hareketler = group_hareketler(df)

# Gruplanmış hareketleri yazdırın
for hareket in grouped_hareketler:
    if len(hareket) == 3:
        direction, count, duration = hareket
        print(f"{direction} hareket ({count} kez): {duration}")
    else:
        direction, duration = hareket
        print(f"{direction} hareket: {duration}")


Left hareket (3 kez): 0 days 00:00:00.736800
Right hareket (2 kez): 0 days 00:00:00.169103
Left hareket: 0 days 00:00:00.100397


In [185]:
grouped_hareketler = group_hareketler(df_hand)


In [186]:
# Gruplanmış hareketler
for hareket in grouped_hareketler:
    if len(hareket) == 3:
        direction, count, duration = hareket
        print(f"{direction} hareket ({count} kez): {duration}")
    else:
        direction, duration = hareket
        print(f"{direction} hareket: {duration}")

Left hareket (18 kez): 0 days 00:00:00.546157
Left hareket (177 kez): 0 days 00:00:05.871211
Right hareket (118 kez): 0 days 00:00:03.919968
Left hareket (34 kez): 0 days 00:00:02.688327
Left hareket (3 kez): 0 days 00:00:00.112730
Left hareket: 0 days 00:00:00
Left hareket (2 kez): 0 days 00:00:00.471244
Left hareket (14 kez): 0 days 00:00:01.600323
Right hareket (2 kez): 0 days 00:00:00.126832
Right hareket (2 kez): 0 days 00:00:00.059497
Left hareket (2 kez): 0 days 00:00:00.915138
Right hareket (2 kez): 0 days 00:00:00.052866
Left hareket (15 kez): 0 days 00:00:00.914362
Right hareket: 0 days 00:00:00
Left hareket (3 kez): 0 days 00:00:00.114367
Left hareket (12 kez): 0 days 00:00:00.661827
Right hareket (43 kez): 0 days 00:00:03.027090
Left hareket (20 kez): 0 days 00:00:01.975592
Left hareket (28 kez): 0 days 00:00:02.236975
Left hareket (27 kez): 0 days 00:00:02.675895
Right hareket: 0 days 00:00:00
Right hareket (2 kez): 0 days 00:00:00.055197
Right hareket (12 kez): 0 days 00:

In [141]:
grouped_hareketler = group_hareketler(df_face)


### baş hareket sıklığı

In [187]:
# Hareket sıklığını hesaplamak için "value_counts()" fonksiyonunu kullanabiliriz
hareket_sayilari = df_face['direction'].value_counts()

# Hareket sıklıklarını yazdır
print("Hareket Sıklıkları:")
for hareket, sayi in hareket_sayilari.items():
    print(f"{hareket}: {sayi} kez")


Hareket Sıklıkları:
Face Detected: 10772 kez
Left: 3751 kez
Right: 2319 kez
Center: 1579 kez
Unknown: 3 kez


In [142]:
# Gruplanmış hareketler
for hareket in grouped_hareketler:
    if len(hareket) == 3:
        direction, count, duration = hareket
        print(f"{direction} hareket ({count} kez): {duration}")
    else:
        direction, duration = hareket
        print(f"{direction} hareket: {duration}")

Left hareket (18 kez): 0 days 00:00:00.546157
Left hareket (177 kez): 0 days 00:00:05.871211
Right hareket (118 kez): 0 days 00:00:03.919968
Left hareket (34 kez): 0 days 00:00:02.688327
Left hareket (3 kez): 0 days 00:00:00.112730
Left hareket: 0 days 00:00:00
Left hareket (2 kez): 0 days 00:00:00.471244
Left hareket (14 kez): 0 days 00:00:01.600323
Right hareket (2 kez): 0 days 00:00:00.126832
Right hareket (2 kez): 0 days 00:00:00.059497
Left hareket (2 kez): 0 days 00:00:00.915138
Right hareket (2 kez): 0 days 00:00:00.052866
Left hareket (15 kez): 0 days 00:00:00.914362
Right hareket: 0 days 00:00:00
Left hareket (3 kez): 0 days 00:00:00.114367
Left hareket (12 kez): 0 days 00:00:00.661827
Right hareket (43 kez): 0 days 00:00:03.027090
Left hareket (20 kez): 0 days 00:00:01.975592
Left hareket (28 kez): 0 days 00:00:02.236975
Left hareket (27 kez): 0 days 00:00:02.675895
Right hareket: 0 days 00:00:00
Right hareket (2 kez): 0 days 00:00:00.055197
Right hareket (12 kez): 0 days 00:

In [143]:
grouped_hareketler = group_hareketler(df_iris)


In [144]:
# Gruplanmış hareketleri yazdırın
for hareket in grouped_hareketler:
    if len(hareket) == 3:
        direction, count, duration = hareket
        print(f"{direction} hareket ({count} kez): {duration}")
    else:
        direction, duration = hareket
        print(f"{direction} hareket: {duration}")

Right hareket (3 kez): 0 days 00:00:00.060176
Left hareket (2 kez): 0 days 00:00:00.055997
Right hareket: 0 days 00:00:00
Left hareket: 0 days 00:00:00
Right hareket (2 kez): 0 days 00:00:00.055991
Left hareket: 0 days 00:00:00
Right hareket: 0 days 00:00:00
Left hareket (3 kez): 0 days 00:00:00.064007
Right hareket: 0 days 00:00:00
Left hareket (2 kez): 0 days 00:00:00.047994
Right hareket: 0 days 00:00:00
Left hareket (4 kez): 0 days 00:00:00.064002
Right hareket: 0 days 00:00:00
Left hareket (3 kez): 0 days 00:00:00.063992
Right hareket: 0 days 00:00:00
Left hareket (5 kez): 0 days 00:00:00.128015
Right hareket: 0 days 00:00:00
Left hareket: 0 days 00:00:00
Right hareket: 0 days 00:00:00
Left hareket (7 kez): 0 days 00:00:00.192032
Right hareket: 0 days 00:00:00
Left hareket (14 kez): 0 days 00:00:00.424037
Right hareket: 0 days 00:00:00
Left hareket (12 kez): 0 days 00:00:00.304037
Right hareket: 0 days 00:00:00
Left hareket: 0 days 00:00:00
Right hareket: 0 days 00:00:00
Left hare

In [161]:
import pandas as pd

# Veri çerçevelerini birleştirin
df_merged = pd.concat([df_hand, df_face, df_iris])

# Ortak ID'lere göre gruplayın
grouped = df_merged.groupby('id')

# Hareketleri ID numaralarına göre yazdırın
for id, group in grouped:
    # Gruplanmış hareketlerin başlangıç ve bitiş zamanlarını alın
    start_time = group['start_time'].min()
    end_time = group['end_time'].max()
    
    # Hareketin bilgilerini yazdırın
    print(f"Hareket ID: {id}")
    print(f"Zaman Aralığı: {start_time} - {end_time}")
    print("Hareketler:")
    
    for index, row in group.iterrows():
        print(f"{row['direction']} hareket ")
    
    print("------")


Hareket ID: 1
Zaman Aralığı: 2023-06-15 01:56:55.070381 - 2023-06-15 02:20:45.116573
Hareketler:
Left hareket 
Left hareket 
Right hareket 
------
Hareket ID: 2
Zaman Aralığı: 2023-06-15 01:56:55.078380 - 2023-06-15 02:20:45.153527
Hareketler:
Left hareket 
Left hareket 
Right hareket 
------
Hareket ID: 3
Zaman Aralığı: 2023-06-15 01:56:55.130557 - 2023-06-15 02:20:45.176956
Hareketler:
Left hareket 
Left hareket 
Right hareket 
------
Hareket ID: 4
Zaman Aralığı: 2023-06-15 01:56:55.138549 - 2023-06-15 02:20:45.198998
Hareketler:
Left hareket 
Left hareket 
Left hareket 
------
Hareket ID: 5
Zaman Aralığı: 2023-06-15 01:56:55.194546 - 2023-06-15 02:20:45.230557
Hareketler:
Left hareket 
Left hareket 
Left hareket 
------
Hareket ID: 6
Zaman Aralığı: 2023-06-15 01:56:55.202543 - 2023-06-15 02:20:45.279351
Hareketler:
Left hareket 
Left hareket 
Right hareket 
------
Hareket ID: 7
Zaman Aralığı: 2023-06-15 01:56:55.250565 - 2023-06-15 02:20:45.311087
Hareketler:
Left hareket 
Left hare

Hareket ID: 6460
Zaman Aralığı: 2023-06-15 03:26:58.705484 - 2023-06-15 04:01:35.692384
Hareketler:
Face Detected hareket 
Face Detected hareket 
Left hareket 
------
Hareket ID: 6461
Zaman Aralığı: 2023-06-15 03:26:58.746715 - 2023-06-15 04:01:35.780963
Hareketler:
Face Detected hareket 
Face Detected hareket 
Left hareket 
------
Hareket ID: 6462
Zaman Aralığı: 2023-06-15 03:26:58.754880 - 2023-06-15 04:01:35.780963
Hareketler:
Face Detected hareket 
Face Detected hareket 
Left hareket 
------
Hareket ID: 6463
Zaman Aralığı: 2023-06-15 03:26:58.805274 - 2023-06-15 04:01:35.862873
Hareketler:
Face Detected hareket 
Face Detected hareket 
Left hareket 
------
Hareket ID: 6464
Zaman Aralığı: 2023-06-15 03:26:58.813276 - 2023-06-15 04:01:35.864879
Hareketler:
Face Detected hareket 
Face Detected hareket 
Left hareket 
------
Hareket ID: 6465
Zaman Aralığı: 2023-06-15 03:26:58.862258 - 2023-06-15 04:01:35.945698
Hareketler:
Face Detected hareket 
Face Detected hareket 
Left hareket 
-----

Hareket ID: 11491
Zaman Aralığı: 2023-06-15 03:29:12.359072 - 2023-06-15 04:05:35.269234
Hareketler:
Face Detected hareket 
Face Detected hareket 
Right hareket 
------
Hareket ID: 11492
Zaman Aralığı: 2023-06-15 03:29:12.367251 - 2023-06-15 04:05:35.352351
Hareketler:
Face Detected hareket 
Face Detected hareket 
Right hareket 
------
Hareket ID: 11493
Zaman Aralığı: 2023-06-15 03:29:12.408389 - 2023-06-15 04:05:35.360476
Hareketler:
Face Detected hareket 
Face Detected hareket 
Right hareket 
------
Hareket ID: 11494
Zaman Aralığı: 2023-06-15 03:29:12.416654 - 2023-06-15 04:05:35.445698
Hareketler:
Face Detected hareket 
Face Detected hareket 
Right hareket 
------
Hareket ID: 11495
Zaman Aralığı: 2023-06-15 03:29:12.459482 - 2023-06-15 04:05:35.445698
Hareketler:
Face Detected hareket 
Face Detected hareket 
Right hareket 
------
Hareket ID: 11496
Zaman Aralığı: 2023-06-15 03:29:12.467482 - 2023-06-15 04:05:35.532391
Hareketler:
Face Detected hareket 
Face Detected hareket 
Right ha

In [174]:
from reportlab.lib.pagesizes import letter
from reportlab.pdfgen import canvas

def create_report(df):
    # Rapor oluşturma
    c = canvas.Canvas("rapor3.pdf", pagesize=letter)

    # Rapor başlığı
    c.setFont("Helvetica-Bold", 16)
    c.drawString(100, 700, "Hareket Raporu")

    # Hareketleri yazdırma
    c.setFont("Helvetica", 12)
    y = 650  # Y koordinatı

    # Verileri rapora yazdırma
    grouped = df.groupby('id')
    for id, group in grouped:
        start_time = group['start_time'].min()
        end_time = group['end_time'].max()

        c.drawString(100, y, f"Hareket ID: {id}")
        c.drawString(100, y-20, f"Zaman Aralığı: {start_time} - {end_time}")
        c.drawString(100, y-40, "El Hareketi /nYüz Hareketi /nGöz Hareketi :")
      

        hareketler = group['direction']
        for hareket in hareketler:
            c.drawString(120, y-60, hareket)
            y -= 20

        c.drawString(100, y-80, "------")
        y -= 100

    # Raporu kaydetme
    c.save()



In [175]:
# Rapor oluşturma işlemini çağırma
create_report(df_merged)